In [ ]:
import matplotlib
%matplotlib inline
import numpy
import os
# Create once the collection for this notebook
collection_id = None
import SEAScope.lib.utils
SEAScope.lib.utils.init_ids(30, 3000)

## Load and select data
<span style="color:green">**Select the Ekman and geostrophic currents generated with previous notebooks on the day you want to compute total current on SEAScope**<br>
**Draw a polygon on SEAScope**<br>
**Click on the extract button on the polygon window**<br>
</span>


In [ ]:
# Load data directly from viewer memory
from SEAScope.lib import get_extracted_data
extractions = get_extracted_data()
granule_id = None

**Load an old data data directly from a serialized extraction using the path printed on terminal <br>
(eg data_path = '/tmp/tmpcdemmhcb20170621TJun061498041719/seascope_extract.pyo')** <br>
Uncomment the following cell and fill data_path value

#from SEAScope.lib import load_pyo
#data_path = ''
#extractions = load_pyo(data_path)
## Print a list of path of extracted granules 
print('\n'.join(extractions.keys()))

**Print selected granules**

In [ ]:
for k, data in enumerate(extractions.keys()):
    print('{} - {}'.format(k, os.path.basename(data)))
    print('\n'.join(['\t{}'.format(x) for x in extractions[data]['data']]))

<span style="color:red">**Choose number corresponding to geostrophic (k_geo) and Ekman (k_ekm) current**</span>

In [ ]:
k_geo = 1 # /!\ You may need to adapt this variable
k_ekm = 0 # /!\ You may need to adapt this variable

In [ ]:
# Load geostrophic current
granule_uri =  next( v for i, v in enumerate(extractions.keys()) if i == k_geo)
extraction = extractions[granule_uri]
data_u1 = extraction['data']['u_geo']
data_v1 = extraction['data']['v_geo']

#Load Ekman current
granule_uri =  next( v for i, v in enumerate(extractions.keys()) if i == k_ekm)
extraction = extractions[granule_uri]
data_u2 = extraction['data']['u_ekm']
data_v2 = extraction['data']['v_ekm']
gcps = extraction['meta']['gcps']

# Get longitudes and latitudes from gcps
from SEAScope.lib.utils import get_lonlat
lon2D, lat2D = get_lonlat(extraction, numpy.shape(data_u1))

## Play with the data
** Compute Total current: <br>
$ \vec{U_{total}} = \vec{U_{geostrophic}} +\vec{U_{ekman}}$
**

In [ ]:
# Compute Total current
utot = data_u1 + data_u2
vtot = data_v1 + data_v2

**Plot variables <br>
<span style="color:red">You can try to plot uekm (zonal componant), vekm (meridional componant), the velocity norm, the norm of the wind ... <br>
Compare your plots with the one from geostrophy </span>**

In [ ]:
matplotlib.pyplot.pcolormesh(lon2D, lat2D,  utot,cmap='jet')  
matplotlib.pyplot.colorbar() 

## Export velocity to SEAScope

In [ ]:
import json
import datetime
import numpy
import seascope_export
from SEAScope.lib.utils import create_collection, create_variable
from SEAScope.lib.utils import create_granule, set_field

**Define Collection:** <br>
** A granule has to belong to a collection **<br>
<span style="color:red"> **Enter a name for the collection (collection_name)**</span>

In [ ]:
if collection_id is None:
    # Collection
    collection_name = 'User - Total current'
    # Create collection
    collection_id, collection = create_collection(collection_name)
print(collection_id)

**Upload granule to SEAScope: <br>
Define shell of granule, create granule <br>
The granule will contain each matrix of modified data as what we call a "field"<br>**
<span style="color:red">** Enter a name for each field (field_name_u and field_name_v) **</span></br>
**Upload collection and granule to SEAScope**

In [ ]:
# Create shell of Granule (where and when granule will appear)
#Start time of granule 
dtstart = extraction['meta']['start']
#End time of granule 
dtstop = extraction['meta']['stop']
# Create granule
if granule_id is None:
    granule_id, granule = create_granule(collection_id, gcps, dtstart, dtstop)

# Set variables
# Enter a name for each variable field
field_name_u = 'u_tot'
field_name_v = 'v_tot'
set_field(granule, field_name_u, utot)
set_field(granule, field_name_v, vtot)   

#Upload collection and granule to SEAScope
seascope_export.upload_granule(collection, granule)

**Telling SEAScope what to display: <br>
 The next step is variables definition. A variable may be composed of
one or two fields (in which case they are considered to be meridional and
zonal components of a vector).** <br>
**<span style="color:red"> Enter a name for each variable you want to display (variable_name_u,  variable_name_u, and variable_name_norm) </span>**</br>

In [ ]:
# Create a variable for the horizontal component
variable_name_u = 'Zonal total current'
tmp = create_variable(collection, variable_name_u, [field_name_u])
if tmp is not None:
    u_variable = tmp
else: 
    print()
    raise Exception('See issues above')
    
# Create a variable for the vertical component
variable_name_v =  'Meridional total current'
tmp = create_variable(collection, variable_name_v, [field_name_v])
if tmp is not None:
    v_variable = tmp
else: 
    print()
    raise Exception('See issues above')
    
# Create a variable for the complete vector
variable_name_norm = 'Norm of total current'
tmp = create_variable(collection, variable_name_norm,
                                  [field_name_u, field_name_v])
if tmp is not None:
    norm_variable = tmp
else: 
    print()
    raise Exception('See issues above')

# Upload variables to SEAScope
seascope_export.upload_variable(u_variable)
seascope_export.upload_variable(v_variable)
seascope_export.upload_variable(norm_variable)

** Telling SEAScope how to display variables: <br>
The rendering options are defined in the following cell. <br>
<span style="color:red"> You can play with min, max values, the colormap ... and check how the rendering changes on SEAScope </span>
**

In [ ]:
# Rendering configuration for the zonal component
u_rcfg = u_variable['rendering']
u_rcfg['min'] = numpy.min(utot)
u_rcfg['max'] = numpy.max(utot)
u_rcfg['colormap'] = 'jet'

# Rendering configuration for the meridional component
v_rcfg = v_variable['rendering']
v_rcfg['min'] = numpy.min(vtot)
v_rcfg['max'] = numpy.max(vtot)
v_rcfg['colormap'] = 'jet'
v_rcfg['opacity'] = 0.3
v_rcfg['filterMode'] = 'BILINEAR'

# Rendering configuration for the complete vector
norm_rcfg = norm_variable['rendering']
norm_rcfg['min'] = 0.0
norm_rcfg['max'] = 2.5
norm_rcfg['colormap'] = 'jet'

# Upload to SEAScope
seascope_export.upload_config(u_rcfg)
seascope_export.upload_config(v_rcfg)
seascope_export.upload_config(norm_rcfg)

<span style="color:green">** Go back to SEAScope and visually compare your total current with GlobCurrent total current.<br> 
play with range, colorbar, transparency ...**</span>